<a href="https://colab.research.google.com/github/tranhuuan170302/Recommended-system-of-information-technology-jobs-at-Viet-Nam/blob/main/model_BERTopic.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
# Install bertopic
!pip install bertopic

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 103.9/103.9 KB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.2/5.2 MB 44.3 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 86.0/86.0 KB 11.7 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 662.4/662.4 KB 47.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 88.2/88.2 KB 10.8 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.3/6.3 MB 75.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 66.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 190.3/190.3 KB 1.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

In [ ]:
# Install older version of joblib
!pip install --upgrade joblib==1.1.0

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
# Data processing
import pandas as pd
import numpy as np

# Text preprocessiong
import nltk
nltk.download('stopwords')
nltk.download('omw-1.4')
nltk.download('wordnet')
wn = nltk.WordNetLemmatizer()

# Topic model
from bertopic import BERTopic

# Dimension reduction
from umap import UMAP

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package omw-1.4 to /root/nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [ ]:
text = pd.read_csv('/content/drive/MyDrive/indeed/resultData.csv')

In [ ]:
text.head()

Unnamed: 0                              JobTitle            Company  \
0           0                        .Net Developer           SmartDev   
1           1            Intern / Fresher Developer     DXC Technology   
2           2  .NET Developer (Middle/Senior level)              SIOUX   
3           3         Jun/Mid/Senior .NET Developer  Saigon Technology   
4           4     Web Developer (.NET, ASP.NET, C#)           NPV Corp   

                Location                      PostDate ExtractDate  \
0                Ðà Nẵng    Posted\nPosted 14 days ago  2023-01-25   
1  Thành phố Hồ Chí Minh  Employer\nActive 22 days ago  2023-01-25   
2                Ðà Nẵng   Posted\nPosted 30+ days ago  2023-01-25   
3                Ðà Nẵng    Posted\nPosted 18 days ago  2023-01-25   
4                Ðà Nẵng    Posted\nPosted 16 days ago  2023-01-25   

                                             Summary            JobUrl  
0  Company Description\nSmartDev is a leading pro...  .NET Developer\n  
1  Overview:\nHow would you like to join an inter...  .NET Developer\n  
2  Sioux Group was founded in 1996 in the Netherl...  .NET Developer\n  
3  Up to $2,200\nJunior, Middle, Senior\nDa Nang\...  .NET Developer\n  
4  Web Developer (.NET, ASP.NET, C#)\nNPV Corp\nỨ...  .NET Developer\n

In [ ]:
review = text[['Summary', 'JobUrl']]

In [ ]:
review

Summary  \
0     Company Description\nSmartDev is a leading pro...   
1     Overview:\nHow would you like to join an inter...   
2     Sioux Group was founded in 1996 in the Netherl...   
3     Up to $2,200\nJunior, Middle, Senior\nDa Nang\...   
4     Web Developer (.NET, ASP.NET, C#)\nNPV Corp\nỨ...   
...                                                 ...   
4374  Mô tả công việc:\n(Mức lương: 15 - 45 triệu VN...   
4375  Giới thiệu:\n...\nJob description:\nWe are str...   
4376  Giới thiệu:\nViệc Ơi It Client\n\nlà công ty 1...   
4377  Mô tả công việc:\n(Mức lương: Thỏa thuận)\nDev...   
4378  Permanent\nFull-time\nHo Chi Minh City\nSOFTWA...   

                          JobUrl  
0               .NET Developer\n  
1               .NET Developer\n  
2               .NET Developer\n  
3               .NET Developer\n  
4               .NET Developer\n  
...                          ...  
4374  Full Stack Web Developer\n  
4375  Full Stack Web Developer\n  
4376  Full Stack Web Developer\n  
4377  Full Stack Web Developer\n  
4378  Full Stack Web Developer\n  

[4379 rows x 2 columns]

In [ ]:
review['Summary'] = review['Summary'].str.replace('\n', '')
review['JobUrl'] = review['JobUrl'].str.replace('\n', '')

In [ ]:
# Remove stopwords
stopwords = nltk.corpus.stopwords.words('english')

In [ ]:
review = review.reset_index()

In [ ]:
review.head()

index                                            Summary          JobUrl
0      0  Company DescriptionSmartDev is a leading provi...  .NET Developer
1      1  Overview:How would you like to join an interna...  .NET Developer
2      2  Sioux Group was founded in 1996 in the Netherl...  .NET Developer
3      3  Up to $2,200Junior, Middle, SeniorDa NangFull-...  .NET Developer
4      4  Web Developer (.NET, ASP.NET, C#)NPV CorpỨng T...  .NET Developer

In [ ]:
text['Summary'][0]

'Company Description\nSmartDev is a leading provider of global software solutions. The company was established in 2014 and is a wholly owned subsidiary of Verysell Technologies Group (Switzerland).\nSmartDev combines renowned Swiss quality with the Vietnamese passion to provide excellence and value. We brings together smart people both internally and externally to create partnerships that push boundaries and challenge the status quo.\nAs part of SmartDev’s aggressive growth plan we are looking to expand our development team, we (https://smartdev.com/) offers tailor-made mobile apps and websites with the most popular frontend and back-end technologies. We are currently works with about 140 developers.\n\nJob Description\n\nYou will report to PM (Project Manager)\nCollaborate with teams to product software design and architecture\nWrite clean, scalable code using .Net programming languages\nTest and deploy application and systems\nRevise, update, refactor and debugs code\nDevelop documen

In [ ]:
import re
from nltk.stem import PorterStemmer
from nltk import pos_tag

In [ ]:
# got these keywords by looking at some examples and using existing knowledge.
tool_keywords1 = ['sql', 'linqpad', 'teamcity', 'octopus', 'ncrunch', 'nuget', 'nunit', 'omnisharp', 'jetBrains rider', 'windbg', '.net reflector',
                  'reSharper', 'python', 'pytorch', 'sql', 'mxnet', 'mlflow', 'einstein', 'theano', 'pyspark', 'solr', 'mahout', 'html', 'css',
                  'cassandra', 'aws', 'powerpoint', 'spark', 'pig', 'sas', 'java', 'nosql', 'docker', 'salesforce', 'scala', 'r',
                  'c', 'c++', 'net', 'tableau', 'pandas', 'scikitlearn', 'sklearn', 'matlab', 'scala', 'keras', 'tensorflow', 'clojure',
                  'caffe', 'scipy', 'numpy', 'matplotlib', 'vba', 'spss', 'linux', 'azure', 'cloud', 'gcp', 'mongodb', 'mysql', 'oracle', 
                  'redshift', 'snowflake', 'kafka', 'javascript', 'qlik', 'jupyter', 'perl', 'bigquery', 'unix', 'react',
                  'scikit', 'powerbi', 's3', 'ec2', 'lambda', 'ssrs', 'kubernetes', 'hana', 'spacy', 'tf', 'django', 'sagemaker',
                  'seaborn', 'mllib', 'github', 'git', 'elasticsearch', 'splunk', 'airflow', 'looker', 'rapidminer', 'birt', 'pentaho', 
                  'jquery', 'nodejs', 'd3', 'plotly', 'bokeh', 'xgboost', 'rstudio', 'shiny', 'dash', 'h20', 'h2o', 'hadoop', 'mapreduce', 
                  'hive', 'cognos', 'angular', 'nltk', 'flask', 'node', 'firebase', 'bigtable', 'rust', 'php', 'cntk', 'lightgbm', 
                  'kubeflow', 'rpython', 'unixlinux', 'postgressql', 'postgresql', 'postgres', 'hbase', 'dask', 'ruby', 'julia', 'tensor',
                  # added r packages doesn't seem to impact the result
                  'dplyr','ggplot2','esquisse','bioconductor','shiny','lubridate','knitr','mlr','quanteda','dt','rcrawler','caret','rmarkdown',
                  'leaflet','janitor','ggvis','plotly','rcharts','rbokeh','broom','stringr','magrittr','slidify','rvest',
                  'rmysql','rsqlite','prophet','glmnet','text2vec','snowballc','quantmod','rstan','swirl','datasciencer', 'amazon web services', 'google cloud', 'sql server',
                  
                  
                  
                'statistics', 'cleansing', 'chatbot', 'cleaning', 'blockchain', 'causality', 'correlation', 'bandit', 'anomaly',
                'dashboard', 'geospatial', 'ocr', 'econometrics', 'pca', 'gis', 'svm', 'svd', 'tuning', 'hyperparameter', 'hypothesis',
                'salesforcecom', 'segmentation', 'biostatistics', 'unsupervised', 'supervised', 'exploratory',
                'recommender', 'recommendations', 'research', 'sequencing', 'probability', 'reinforcement', 'graph', 'bioinformatics',
                'chi', 'knn', 'outlier', 'etl', 'normalization', 'classification', 'optimizing', 'prediction', 'forecasting',
                'clustering', 'cluster', 'optimization', 'visualization', 'nlp', 'c#', 'negotiation', 'self learning', 
                'regression', 'logistic', 'nn', 'cnn', 'glm', 'sloving', 'ux ui', 'teamwork', 'creative thinking',
                'rnn', 'lstm', 'gbm', 'boosting', 'recurrent', 'convolutional', 'bayesian',
                'bayes', 'random forest', 'natural language processing', 'machine learning', 'decision tree', 'deep learning', 'experimental design',
                'time series', 'nearest neighbors', 'neural network', 'support vector machine', 'computer vision', 'machine vision', 'dimensionality reduction', 
                'text analytics', 'power bi', 'a/b testing', 'ab testing', 'chat bot', 'data mining',
                
                
                'bs', 'bachelor', 'undergraduate', 'certificate',
               'master', 'graduate', 'mba', 'intermediate',
               'phd', 'ph.d', 'ba', 'ma', 'it',
               'postdoctoral', 'postdoc', 'doctorate', 'new graduate', 'đại học']


In [ ]:
ps = PorterStemmer()
tool_keywords1_set = set([ps.stem(tok) for tok in tool_keywords1])

In [ ]:

df = pd.DataFrame(columns = ['index', 'review'])
for idx in review.index.unique():
  string = review['Summary'][idx]
  string = string.split('.')
  id = []
  txt = []
  
  for st in string:
    id.append(idx)
    txt.append(st)
    datax = pd.DataFrame(list(zip(id, txt)), columns = ['index', 'review'])
  df = pd.concat([df, datax])

In [ ]:
df

index                                             review
0      0  Company DescriptionSmartDev is a leading provi...
1      0   The company was established in 2014 and is a ...
2      0  SmartDev combines renowned Swiss quality with ...
3      0   We brings together smart people both internal...
4      0  As part of SmartDev’s aggressive growth plan w...
..   ...                                                ...
8   4378   Scrum Developer, Scrum Master)You can contrib...
9   4378   We regularly exchange ideas, give each other ...
10  4378   From this, you'll gather that we communicate ...
11  4378  Added to this is an attractive benefits packag...
12  4378  Permanent labor contracts with full social ins...

[84890 rows x 2 columns]

In [ ]:
review = review.merge(df, left_on = 'index', right_on = 'index')

In [ ]:
review

index                                            Summary  \
0         0  Company DescriptionSmartDev is a leading provi...   
1         0  Company DescriptionSmartDev is a leading provi...   
2         0  Company DescriptionSmartDev is a leading provi...   
3         0  Company DescriptionSmartDev is a leading provi...   
4         0  Company DescriptionSmartDev is a leading provi...   
...     ...                                                ...   
84885  4378  PermanentFull-timeHo Chi Minh CitySOFTWARE ENG...   
84886  4378  PermanentFull-timeHo Chi Minh CitySOFTWARE ENG...   
84887  4378  PermanentFull-timeHo Chi Minh CitySOFTWARE ENG...   
84888  4378  PermanentFull-timeHo Chi Minh CitySOFTWARE ENG...   
84889  4378  PermanentFull-timeHo Chi Minh CitySOFTWARE ENG...   

                         JobUrl  \
0                .NET Developer   
1                .NET Developer   
2                .NET Developer   
3                .NET Developer   
4                .NET Developer   
...                         ...   
84885  Full Stack Web Developer   
84886  Full Stack Web Developer   
84887  Full Stack Web Developer   
84888  Full Stack Web Developer   
84889  Full Stack Web Developer   

                                                  review  
0      Company DescriptionSmartDev is a leading provi...  
1       The company was established in 2014 and is a ...  
2      SmartDev combines renowned Swiss quality with ...  
3       We brings together smart people both internal...  
4      As part of SmartDev’s aggressive growth plan w...  
...                                                  ...  
84885   Scrum Developer, Scrum Master)You can contrib...  
84886   We regularly exchange ideas, give each other ...  
84887   From this, you'll gather that we communicate ...  
84888  Added to this is an attractive benefits packag...  
84889  Permanent labor contracts with full social ins...  

[84890 rows x 4 columns]

In [ ]:
review = review.loc[review.duplicated() == False, :]

In [ ]:
def filterString(string):
  item = string.split(' ')
  stemmed_tokens = [ps.stem(tok).lower() for tok in item]
  for st in stemmed_tokens:
    if tool_keywords1_set.__contains__(st):
      return string
  return None

In [ ]:
review['review_filter'] = review['review'].apply(lambda string: filterString(string))

In [ ]:
review['review_filter'].isna().sum()

64419

In [ ]:
review.shape

(16723, 5)

In [ ]:
review.dropna(inplace=True)

In [ ]:
# Remove stopwords
review['Summary_without_stopwords'] = review['review'].apply(lambda x: ' '.join([w for w in x.split() if w.lower() not in stopwords]))

# Lemmatization
review['review_lemmatized'] = review['Summary_without_stopwords'].apply(lambda x: ' '.join([wn.lemmatize(w) for w in x.split() if w not in stopwords]))

# Take a look at the data
review.head()

index                                            Summary          JobUrl  \
8      0  Company DescriptionSmartDev is a leading provi...  .NET Developer   
9      0  Company DescriptionSmartDev is a leading provi...  .NET Developer   
10     0  Company DescriptionSmartDev is a leading provi...  .NET Developer   
11     0  Company DescriptionSmartDev is a leading provi...  .NET Developer   
12     0  Company DescriptionSmartDev is a leading provi...  .NET Developer   

                                               review  \
8   Net programming languagesTest and deploy appli...   
9                   Net DeveloperBe familiar with ASP   
10  NET framework, SQL Server and design/ architec...   
11                   Net languages (C#, Visual Basic    
12  Net), and HTML5/ CSS3Be familiar with architec...   

                                        review_filter  \
8   Net programming languagesTest and deploy appli...   
9                   Net DeveloperBe familiar with ASP   
10  NET framework, SQL Server and design/ architec...   
11                   Net languages (C#, Visual Basic    
12  Net), and HTML5/ CSS3Be familiar with architec...   

                            Summary_without_stopwords  \
8   Net programming languagesTest deploy applicati...   
9                        Net DeveloperBe familiar ASP   
10  NET framework, SQL Server design/ architectura...   
11                    Net languages (C#, Visual Basic   
12  Net), HTML5/ CSS3Be familiar architecture styl...   

                                    review_lemmatized  
8   Net programming languagesTest deploy applicati...  
9                        Net DeveloperBe familiar ASP  
10  NET framework, SQL Server design/ architectura...  
11                     Net language (C#, Visual Basic  
12  Net), HTML5/ CSS3Be familiar architecture styl...

In [ ]:
review

index                                            Summary  \
8         0  Company DescriptionSmartDev is a leading provi...   
9         0  Company DescriptionSmartDev is a leading provi...   
10        0  Company DescriptionSmartDev is a leading provi...   
11        0  Company DescriptionSmartDev is a leading provi...   
12        0  Company DescriptionSmartDev is a leading provi...   
...     ...                                                ...   
84872  4377  Mô tả công việc:(Mức lương: Thỏa thuận)Develop...   
84874  4377  Mô tả công việc:(Mức lương: Thỏa thuận)Develop...   
84877  4378  PermanentFull-timeHo Chi Minh CitySOFTWARE ENG...   
84883  4378  PermanentFull-timeHo Chi Minh CitySOFTWARE ENG...   
84889  4378  PermanentFull-timeHo Chi Minh CitySOFTWARE ENG...   

                         JobUrl  \
8                .NET Developer   
9                .NET Developer   
10               .NET Developer   
11               .NET Developer   
12               .NET Developer   
...                         ...   
84872  Full Stack Web Developer   
84874  Full Stack Web Developer   
84877  Full Stack Web Developer   
84883  Full Stack Web Developer   
84889  Full Stack Web Developer   

                                                  review  \
8      Net programming languagesTest and deploy appli...   
9                      Net DeveloperBe familiar with ASP   
10     NET framework, SQL Server and design/ architec...   
11                      Net languages (C#, Visual Basic    
12     Net), and HTML5/ CSS3Be familiar with architec...   
...                                                  ...   
84872   is a plusExperience with Jest to write E2E te...   
84874                Experience with Git / GitHub, Agile   
84877  PermanentFull-timeHo Chi Minh CitySOFTWARE ENG...   
84883  What you will doAs a Senior Fullstack Java Sof...   
84889  Permanent labor contracts with full social ins...   

                                           review_filter  \
8      Net programming languagesTest and deploy appli...   
9                      Net DeveloperBe familiar with ASP   
10     NET framework, SQL Server and design/ architec...   
11                      Net languages (C#, Visual Basic    
12     Net), and HTML5/ CSS3Be familiar with architec...   
...                                                  ...   
84872   is a plusExperience with Jest to write E2E te...   
84874                Experience with Git / GitHub, Agile   
84877  PermanentFull-timeHo Chi Minh CitySOFTWARE ENG...   
84883  What you will doAs a Senior Fullstack Java Sof...   
84889  Permanent labor contracts with full social ins...   

                               Summary_without_stopwords  \
8      Net programming languagesTest deploy applicati...   
9                           Net DeveloperBe familiar ASP   
10     NET framework, SQL Server design/ architectura...   
11                       Net languages (C#, Visual Basic   
12     Net), HTML5/ CSS3Be familiar architecture styl...   
...                                                  ...   
84872  plusExperience Jest write E2E test code plusEx...   
84874                     Experience Git / GitHub, Agile   
84877  PermanentFull-timeHo Chi Minh CitySOFTWARE ENG...   
84883  doAs Senior Fullstack Java Software Engineer b...   
84889  Permanent labor contracts full social insuranc...   

                                       review_lemmatized  
8      Net programming languagesTest deploy applicati...  
9                           Net DeveloperBe familiar ASP  
10     NET framework, SQL Server design/ architectura...  
11                        Net language (C#, Visual Basic  
12     Net), HTML5/ CSS3Be familiar architecture styl...  
...                                                  ...  
84872  plusExperience Jest write E2E test code plusEx...  
84874                     Experience Git / GitHub, Agile  
84877  PermanentFull-timeHo Chi Minh CitySOFTWARE ENG...  
84883  doAs Senior Fullstack Java Softw

In [ ]:
review['review'].isna().sum()

0

In [ ]:
review = review.loc[review.duplicated() == False, :]

In [ ]:
review = review.reset_index()

In [ ]:
# Initiate UMAP
umap_model = UMAP(n_neighbors=15, 
                  n_components=5, 
                  min_dist=0.0, 
                  metric='cosine', 
                  random_state=100)

# Initiate BERTopic
topic_model = BERTopic(umap_model=umap_model, language="english", calculate_probabilities=True)

# Run BERTopic model
topics, probabilities = topic_model.fit_transform(review['review_lemmatized'])

In [ ]:
# Get the list of topics
topic_model.get_topic_info()

Topic  Count                                            Name
0       -1   2881                        -1_data_business_vin_nng
1        0    464                      0_thiuvic_clientl_tphcm_nc
2        1    462                                 1_ch_du_phc_khi
3        2    457          2_remote_rails_nnmanyear_developerupto
4        3     99                     3_gcp_cloud_azure_29yearend
..     ...    ...                                             ...
535    534     11            534_markup_userfriendly_thunuse_page
536    535     11         535_vnaxon_organizer_httpsdevday_devday
537    536     11     536_seminartraining_recreation_lesson_drink
538    537     11  537_negotiation_salaryup_negotiable_candidates
539    538     11                   538_rdbms_postgresql_truy_cch

[540 rows x 3 columns]

In [ ]:
# Get top 10 terms for a topic
topic_model.get_topic(0)

[('thiuvic', 0.04991163059391445),
 ('clientl', 0.04991163059391445),
 ('tphcm', 0.04923284682399324),
 ('nc', 0.046331696344846005),
 ('ngoi', 0.04430818732147282),
 ('lnh', 0.042607517241428604),
 ('100', 0.04086305842331315),
 ('hot', 0.03859421612549335),
 ('vc', 0.037714483150244886),
 ('mm', 0.03532342943287017)]

In [ ]:
# Visualize top topic keywords
topic_model.visualize_barchart(top_n_topics=20)

In [ ]:
# Visualize term rank decrease
topic_model.visualize_term_rank()

In [ ]:
# Visualize intertopic distance
topic_model.visualize_topics()

In [ ]:
# Visualize connections between topics using hierachical clustering
topic_model.visualize_hierarchy(top_n_topics=15)

In [ ]:
# Visualize similarity using heatmap
topic_model.visualize_heatmap()

In [ ]:
# Visualize probability distribution
topic_model.visualize_distribution(topic_model.probabilities_[0], min_probability=0.015)

In [ ]:
# Check the content for the first review
review['review'][0]

'Company DescriptionSmartDev is a leading provider of global software solutions'

In [ ]:
# Get probabilities for all topics
topic_model.probabilities_[0]

array([0.00044885, 0.00444971, 0.00293378, 0.00508692, 0.00209823,
       0.00375478, 0.00062205, 0.00644959, 0.00232   , 0.00246775,
       0.00398393, 0.00156436, 0.00162212, 0.00202011, 0.00191184,
       0.00287072, 0.00336815, 0.00169304, 0.00157997, 0.00125588,
       0.00207537, 0.00246164, 0.001972  , 0.00216574, 0.00282832,
       0.00212871, 0.00193225, 0.0014066 , 0.00379668, 0.00428879,
       0.00179904, 0.00323177, 0.00251701, 0.0028033 , 0.0029986 ,
       0.00191449, 0.00157184, 0.00300223, 0.00066476, 0.00077048,
       0.00102492, 0.00252754, 0.00326037, 0.00301064, 0.00391274,
       0.00364385, 0.00124639, 0.00262816, 0.00163455, 0.00227091,
       0.00170906, 0.00130041, 0.00284544, 0.00177831, 0.09603284,
       0.00468034, 0.00096843, 0.00167888, 0.00349887, 0.00151007,
       0.00274939, 0.00153407, 0.001786  , 0.00517956, 0.00308357,
       0.00362985, 0.00183237, 0.00522239, 0.0045078 , 0.00180078,
       0.0011669 , 0.01186363, 0.00376844, 0.00171544, 0.00140

In [ ]:
len(topic_model.topics_[:])

5000

In [ ]:
# Get the topic predictions
topic_prediction = topic_model.topics_[:]

# Save the predictions in the dataframe
review['topic_prediction'] = topic_prediction

# Take a look at the data
review.head()

level_0 index                                            Summary  \
0        0     0  Company DescriptionSmartDev is a leading provi...   
1        1     0  Company DescriptionSmartDev is a leading provi...   
2        2     0  Company DescriptionSmartDev is a leading provi...   
3        3     0  Company DescriptionSmartDev is a leading provi...   
4        4     0  Company DescriptionSmartDev is a leading provi...   

           JobUrl                                             review  \
0  .NET Developer  Company DescriptionSmartDev is a leading provi...   
1  .NET Developer   The company was established in 2014 and is a ...   
2  .NET Developer  SmartDev combines renowned Swiss quality with ...   
3  .NET Developer   We brings together smart people both internal...   
4  .NET Developer  As part of SmartDev’s aggressive growth plan w...   

                           Summary_without_stopwords  \
0  Company DescriptionSmartDev leading provider g...   
1  company established 2014 wholly owned subsidia...   
2  SmartDev combines renowned Swiss quality Vietn...   
3  brings together smart people internally extern...   
4  part SmartDev’s aggressive growth plan looking...   

                                   review_lemmatized  topic_prediction  
0  Company DescriptionSmartDev leading provider g...                54  
1  company established 2014 wholly owned subsidia...                54  
2  SmartDev combine renowned Swiss quality Vietna...                71  
3  brings together smart people internally extern...                -1  
4  part SmartDev’s aggressive growth plan looking...                29

In [ ]:
review['review'][3000]

', Other, Ho Chi MinhXem bản đồTại văn phòng38 ngày trướcMô Tả Công ViệcPhát triển các dự án phần mềm trên nền tảng ASP'

In [ ]:
# New data for the review
new_review = "Experienced in front-end (CSS3 / HTML5 / JavaScript), JavaScript libraries (jQuery). Have knowledge of the TypeScript is a plus"

# Find topics
num_of_topics = 3
similar_topics, similarity = topic_model.find_topics(new_review, top_n=num_of_topics); 

# Print results
print(f'The top {num_of_topics} similar topics are {similar_topics}, and the similarities are {np.round(similarity,2)}')

The top 3 similar topics are [25, 20, 81], and the similarities are [0.55 0.49 0.44]


In [ ]:
# Print the top keywords for the top similar topics
for i in range(num_of_topics):
  print(f'The top keywords for topic {similar_topics[i]} are:')
  print(topic_model.get_topic(similar_topics[i]))

The top keywords for topic 25 are:
[('javascript', 0.14508227133319854), ('css', 0.11898275902174014), ('html5', 0.08408669050139603), ('html', 0.07574016885759279), ('jquery', 0.07090471994595711), ('css3', 0.05243679965988032), ('typescript', 0.051148436248073234), ('modern', 0.046802670014343385), ('responsive', 0.046802670014343385), ('experience', 0.03901767965707461)]
The top keywords for topic 20 are:
[('reactjs', 0.1082987432017377), ('angular', 0.08849778501685382), ('angularjs', 0.0718159268840518), ('frontend', 0.07171792274556334), ('vue', 0.06467254258148634), ('react', 0.06129454550533264), ('vuejs', 0.059869113227990975), ('framework', 0.04429165706207272), ('es6', 0.03955552239698917), ('plus', 0.038877203535984506)]
The top keywords for topic 81 are:
[('jquery', 0.10828530942128278), ('mvc', 0.07634201293149089), ('html', 0.06729889812995266), ('entity', 0.06289230933734226), ('javascript', 0.06042787350853165), ('framework', 0.04587814624632782), ('mvcbasic', 0.042535

In [ ]:
review.loc[review['topic_prediction'] == 25, 'JobUrl'].unique()[0]

'.NET Developer'